In [78]:
class Graph:
    def __init__(self):
        self.adj_dict = {}
        self.node_dict = {}
        self.edge_list = []
        
    def add_edge(self, v, u, pattern):
        if v not in self.adj_dict:
            self.adj_dict[v] = {u:pattern}
        else:
            self.adj_dict[v][u] = pattern
            
        if u not in self.adj_dict:
            self.adj_dict[u] = {v:pattern}
        else:
            self.adj_dict[u][v] = pattern
            
        if v not in self.node_dict:
            self.node_dict[v] = v
            
        if u not in self.node_dict:
            self.node_dict[u] = u
        
        self.edge_list.append([v,u])
        
    def del_edge(self, v, u):
        if u in self.adj_dict[v]:
            del(self.adj_dict[v][u])
            
        if v in self.adj_dict[u]:
            del(self.adj_dict[u][v])
            
    def del_uedge(self, v, u):
        if v in self.adj_dict[u]:
            del(self.adj_dict[u][v])
            
    def edge_l(self):
        return self.edge_list
        
    def adj_d(self, v):
        return self.adj_dict[v]
    
    def vertex(self, v):
        self.adj_list = self.adj_dict[v]
        self.deg = len(self.adj_dict[v])
        self.vertex_num = 1
        
        return self.vertex_num, self.deg, self.adj_list
    
import sys
import time

fileName = 'NCI1'

edges_path = './dataset/' + fileName + '/' + fileName + '.edges' #sys.argv[1]
label_path = './dataset/' + fileName + '/' + fileName + '.node_labels' #sys.argv[2]

label_dict = {}
label_kind = []
nodeList = []
pers = 3
pt_fq = {} # 빈발패턴
label_f = open(label_path, 'r')
# node = 1
while True:
    # line = label_f.readline().replace('\n', '').strip()
    line = label_f.readline().replace('\n', '').strip()
    if not line:
        break
    
    node = line.split(',')[0]
    label = line.split(',')[1]
    
    # label = line
    label_dict[str(node)] = label
    label_kind.append(label)
    # node += 1
label_f.close

label_kind = list(set(label_kind))

edge_f = open(edges_path, 'r')
gs = Graph()
while True:
    line = edge_f.readline().replace('\n', '').strip()
    if not line:
        break
    
    v = line.split(',')[0]
    u = line.split(',')[1]
    
    if v == u:
        continue
    
    if v not in label_dict:
        label_dict[v] = '0'
        
    if u not in label_dict:
        label_dict[u] = '0'
    
    nodeList.append(v)
    nodeList.append(u)

    pt = label_dict[v] + '/' + label_dict[u]
    
    re_pt = ''.join(reversed(pt))
    
    if pt not in pt_fq and re_pt not in pt_fq:
        pt_fq[pt] = 1
        gs.add_edge(v,u,pt)
        
    elif re_pt in pt_fq:
        pt_fq[re_pt] = pt_fq[re_pt] + 1
        gs.add_edge(v,u,re_pt)
        
    elif pt in pt_fq:
        pt_fq[pt] = pt_fq[pt] + 1
        gs.add_edge(v,u,pt)

edge_f.close

nodeList = list(set(nodeList))
new_pt_fq = {}
new_pt_fq.update(pt_fq)
p_id = 0
Freq = 0
TF = 0
FR = 0

def Top_nPercent(dict, n):
    if len(dict) == 0:
        return 0
    part_v = len(dict)*n//100 - 1
    value = list(sorted(dict.items(), key = lambda item: item[1], reverse = True))[part_v][1]
    return value

def pattern_gen(ptternFrequency, pttern_th):
    add_pt = {}
    
    for pt1 in ptternFrequency:
        if ptternFrequency[pt1] >= pttern_th:
            pt_tgt = pt1.split('/')
            for pt2 in ptternFrequency:
                if pt1 != pt2 and ptternFrequency[pt2] >= pttern_th:
                    pt_scr = pt2.split('/')
                    between_len = len(pt_tgt) - 2
                    if between_len == 0:
                        if pt_tgt[0] == pt_scr[0]:
                            pt = pt_scr[1] + '/' + pt1
                        elif pt_tgt[0] == pt_scr[1]:
                            pt = pt_scr[0] + '/' + pt1
                        elif pt_tgt[-1] == pt_scr[0]:
                            pt = pt1 + '/' + pt_scr[1]

                        elif pt_tgt[-1] == pt_scr[-1]:
                            pt = pt1 + '/' + pt_scr[0]
                        else:
                            continue
                    else:
                        if pt_tgt[:between_len] == pt_scr[between_len:-1]: #앞, 뒤
                            pt = pt_scr[0] + '/' + pt1
                        elif pt_tgt[between_len:-1] == pt_scr[:between_len]: #뒤, 앞
                            pt = pt1 + '/' + pt_scr[-1]
                        else:
                            continue
                        
                    re_pt = ''.join(reversed(pt))
        
                    if pt not in add_pt and re_pt not in add_pt:
                        add_pt[pt] = min(ptternFrequency[pt1], ptternFrequency[pt2])
    
    return add_pt

def updatePattern(updateDict, pers):
    update_dict = (pattern_gen(updateDict, Top_nPercent(updateDict, pers)))
    if len(update_dict) != 0:
        new_pt_fq.update(update_dict)
        updatePattern(update_dict, pers)
        
print(len(pt_fq))
print(sorted(pt_fq.items(), key = lambda item: item[1], reverse = True)[:100])
updatePattern(pt_fq, pers)
print(len(new_pt_fq))
allEdgeDict = {}

def neighborScore(v, u):
    deg_max = gs.vertex(v)[1]
    same_deg = len((gs.vertex(v)[2].keys() & gs.vertex(u)[2].keys()))
    deg_ratio = gs.vertex(u)[1]/gs.vertex(v)[1]
            
    score = (same_deg/deg_max) + deg_ratio
    
    return score

def pattern_Marge(v):
    score = {}
    neighbor_v = gs.vertex(v)[2]
    
    for u in neighbor_v:
        if u in allEdgeDict:
            continue
        re_pt = ''.join(reversed(neighbor_v[u]))
        if neighbor_v[u] in new_pt_fq.keys() or re_pt in new_pt_fq.keys():
            score[u] = neighborScore(v, u)
    
    if score:
        su = list(sorted(score.items(), key = lambda item: item[1], reverse = True))[0]
        gs.del_edge(v, su[0])
        MargeNode = v + '/' + su[0]
        patternExtension = label_dict[v] + '/' + label_dict[su[0]]
        
        return MargeNode, patternExtension
    else:
        return 0, 0
    
def pattern_Marge2(MargeNode, patternExtension):
    frontV = MargeNode.split('/')[0]
    backV = MargeNode.split('/')[-1]
    frontMax = [0,0]
    backMax = [0,0]
    union_list1 = {}
    union_list2 = {}
    frontScore = {}
    backScore = {}

    for front in gs.vertex(frontV)[2].keys():
        if front in allEdgeDict or backV == front:
            continue
        union_list1[front] = label_dict[front] + '/' + patternExtension
        
    for back in gs.vertex(backV)[2].keys():
        if back in allEdgeDict or frontV == back:
            continue
        union_list2[back] = patternExtension + '/' + label_dict[back]
            
    for union in union_list1.keys():
        re_pt = ''.join(reversed(union_list1[union]))
        if union_list1[union] in new_pt_fq.keys() or re_pt in new_pt_fq.keys():
            frontScore[union] = neighborScore(frontV, union)
            
    for union in union_list2.keys():
        re_pt = ''.join(reversed(union_list2[union]))
        if union_list2[union] in new_pt_fq.keys() or re_pt in new_pt_fq.keys():
            backScore[union] = neighborScore(backV, union)

    if frontScore:
        frontMax = list(sorted(frontScore.items(), key = lambda item: item[1], reverse = True))[0]

    if backScore:
        backMax = list(sorted(backScore.items(), key = lambda item: item[1], reverse = True))[0]
    
    if frontMax[1] >= backMax[1] and frontMax[1] != 0:
        gs.del_edge(frontV, frontMax[0])
        MargeNode = frontMax[0] + '/' + MargeNode
        new_pt = union_list1[frontMax[0]]
        
    elif frontMax[1] < backMax[1] and backMax[1] != 0:
        gs.del_edge(backV, backMax[0])
        MargeNode = MargeNode + '/' + backMax[0]
        new_pt = union_list2[backMax[0]]
        
    else:
        return MargeNode, patternExtension, 0
        
    return MargeNode, new_pt, 1
    
pattern_dict = {}
edge_dict = {}
s1 = time.time()

while(True):
    edgeList = []
    node_size = len(nodeList)
    
    if node_size <= 0:
        e1 = time.time()
        d1 = e1-s1
        print(node_size, d1)
        break
    
    node = nodeList[0]
    newV, pE = pattern_Marge(node)
    
    if newV == 0:
        nodeList.remove(node)
        continue
    
    boolz = 1
    while (boolz > 0):
        newV, pE, boolz = pattern_Marge2(newV, pE)
    
    del_list = newV.split('/')
    for del_one in del_list:
        nodeList.remove(del_one)
        edge_list = list(gs.vertex(del_one)[2].keys())                
        edgeList.extend(edge_list)
        allEdgeDict[del_one] = newV
    
    if pE not in pattern_dict:
        pattern_dict[pE] = [newV]
        edge_dict[newV] = edgeList
    else:
        pattern_dict[pE].append(newV)
        edge_dict[newV] = edgeList
    
for pd in edge_dict:
    for pd2 in edge_dict[pd]:
        if pd2 in allEdgeDict:
            edge_dict[pd].remove(pd2)
            edge_dict[pd].append(allEdgeDict[pd2])

pEdgeList = []
pNodeDict = {}

for pd in edge_dict:
    if pd not in pNodeDict:
        pNodeDict[pd] = pd
    for pd2 in edge_dict[pd]:
        if pd == pd2:
            continue
        pEdgeList.append([pd, pd2])
        if pd2 not in pNodeDict:
            pNodeDict[pd2] = pd2
            


87
[('3/3', 148304), ('3/1', 43368), ('3/2', 37234), ('3/4', 3656), ('2/1', 2024), ('3/5', 1892), ('3/7', 1420), ('2/2', 1404), ('1/4', 1298), ('1/6', 458), ('3/6', 356), ('2/4', 346), ('1/1', 336), ('3/9', 254), ('3/14', 213), ('14/3', 213), ('3/22', 136), ('1/5', 100), ('2/6', 70), ('4/4', 56), ('2/5', 44), ('1/22', 40), ('3/21', 38), ('21/3', 38), ('27/1', 22), ('1/27', 22), ('7/2', 20), ('5/10', 16), ('10/5', 16), ('1/7', 16), ('1/26', 15), ('3/26', 15), ('26/1', 15), ('26/3', 15), ('5/9', 14), ('6/4', 12), ('8/1', 12), ('7/7', 12), ('27/3', 11), ('3/27', 11), ('7/4', 10), ('3/19', 10), ('19/3', 10), ('11/3', 10), ('10/3', 10), ('3/10', 10), ('14/2', 7), ('2/14', 7), ('5/5', 6), ('4/26', 5), ('26/4', 5), ('3/25', 4), ('25/3', 4), ('2/17', 4), ('17/2', 4), ('8/3', 4), ('3/17', 3), ('17/3', 3), ('3/30', 3), ('30/3', 3), ('31/3', 3), ('3/31', 3), ('1/37', 2), ('37/1', 2), ('7/29', 2), ('29/7', 2), ('3/28', 2), ('28/3', 2), ('2/21', 2), ('21/2', 2), ('31/1', 2), ('1/31', 2), ('11/2', 2

In [80]:
# print(pattern_dict)
Gc = []
# Gc.extend(pEdgeList)
print(len(pEdgeList))
print(len(pNodeDict))
print(allEdgeDict['15'])

for v, u in pEdgeList:
    print(v, u)
    if v in edge_dict:
        vEdge = edge_dict[v]
    else:
        vEdge = list(gs.vertex(v)[2].keys())
        for pd in vEdge:
            if pd in allEdgeDict:
                vEdge.remove(pd)
                vEdge.append(allEdgeDict[pd])
        
    if u in edge_dict:
        uEdge = edge_dict[u]
    else:
        uEdge = list(gs.vertex(u)[2].keys())
        for pd in uEdge:
            if pd in allEdgeDict:
                uEdge.remove(pd)
                uEdge.append(allEdgeDict[pd])
        
    print(v, len(vEdge), u, len(uEdge))
#     node = pEdgeList[0]
#     print(node)


104104
79758
10/15
11649/11647 11650
4 2
11649/11647 11664
4 2
11649/11647 11651/11660/11659
4 4
11649/11647 11669/11663
4 2
7411/7438/7425 7424
3 2
7411/7438/7425 7421/7427
3 3
7411/7438/7425 7413/7434/7436
3 3
38432/38426 38419
2 2
38432/38426 38423/38431
2 2
18615/18625/18622 18621
3 2
18615/18625/18622 18621/18623
3 4
18615/18625/18622 18616/18624
3 3
23291/23293 23289
3 2
23291/23293 23272
3 1
23291/23293 23292/23290
3 2
70674/70678/70636 70684
4 2
70674/70678/70636 70695
4 1
70674/70678/70636 70653/70677
4 3
70674/70678/70636 70685/70643
4 2
46654/46656/46644 46646
2 1
46654/46656/46644 46648/46652
2 2
39105/39104 39107
4 1
39105/39104 39097
4 2
39105/39104 39101/39106/39114
4 2
39105/39104 39098/39109
4 3
74500/74508/74473 74479
3 1
74500/74508/74473 74497
3 3
74500/74508/74473 74503/74488/74474
3 2
32267/32261 32257
3 2
32267/32261 32275/32271
3 2
32267/32261 32273/32269
3 2
87641/87648/87646 87645
3 2
87641/87648/87646 87653/87652
3 4
87641/87648/87646 87647/87650
3 2
7554/754

In [68]:
Gs = pEdgeList
f = open('./Result/' + fileName + '_result_us.edges', 'w')


for e in Gs:
    str_e = e[0] + ',' + e[1] + '\n'
    f.write(str_e)
        
f.close()

In [48]:
import networkx as nx
from pyvis.network import Network
G = nx.Graph()

for v, u in pEdgeList:
    G.add_edge(v,u)
    
graph_name = 'dblp_pattern' + '.html'
net = Network(bgcolor="#222222", font_color="white", filter_menu=True, select_menu=True)
net.from_nx(G)

net.show_buttons(filter_=['physics'])
net.show(graph_name)

KeyboardInterrupt: 